In [12]:
import pandas as pd
from pathlib import Path
import numpy as np

# ============================================================
# RUTA DEL ARCHIVO EXCEL
# ============================================================
excel_path = Path(r"C:\Users\julio\OneDrive\Documentos\Trabajo\Ideas Frescas\Proyectos\REM\BD\BD_Mazatlan.xlsm")  # <- AJUSTA A TU RUTA LOCAL

assert excel_path.exists(), f"El archivo {excel_path} no se encontró. Revisa la ruta."

# ============================================================
# 1. CARGA DE DATOS DESDE EXCEL
# ============================================================

# Cargar el libro de Excel
xls = pd.ExcelFile(excel_path)

# Cargar únicamente las hojas que nos interesan
ventas_df         = pd.read_excel(excel_path, sheet_name="Ventas")
precios_df        = pd.read_excel(excel_path, sheet_name="Precios")
vertical_df       = pd.read_excel(excel_path, sheet_name="Vertical")
horizontal_df     = pd.read_excel(excel_path, sheet_name="Horizontal")
lote_df           = pd.read_excel(excel_path, sheet_name="Lote")
amenidades_df     = pd.read_excel(excel_path, sheet_name="Amenidades")  
creditos_df       = pd.read_excel(excel_path, sheet_name="Creditos")

# Hojas de información de prototipos:
info_vert_df      = pd.read_excel(excel_path, sheet_name="Info_Prototipos_vertical")
info_horiz_df     = pd.read_excel(excel_path, sheet_name="Info_Prototipos_horizontal")
info_lote_df      = pd.read_excel(excel_path, sheet_name="Info_Prototipos_lote")


# ============================================================
#  Funciones auxiliares
# ============================================================

#  CÁLCULO DE ABSORCIÓN PROMEDIO MENSUAL POR PROYECTO
def calcular_absorcion_mensual(
    ventas_df,
    vertical_df,
    horizontal_df,
    lote_df,
    col_fecha_ventas="Fecha",
    col_fecha_inicio="Fecha_inicio_venta",
    col_tipo="Tipo_proyecto",
    col_desarrollo="Nombre_desarrollo",
    col_ventas_periodo="Ventas_periodo"
):
    """
    Calcula la absorción promedio mensual por proyecto, usando:
      - ventas_df: hoja Ventas
      - vertical_df, horizontal_df, lote_df: hojas de producto para obtener Fecha_inicio_venta
    
    Lógica:
      - Para cada proyecto (Nombre_desarrollo) y tipo (Tipo_proyecto):
          * Primer registro:
                meses = meses entre Fecha_inicio_venta y primera Fecha en ventas_df
                absorción = Ventas_periodo / meses
          * Registros siguientes:
                meses = meses entre Fecha actual y Fecha anterior de ese desarrollo
                absorción = Ventas_periodo / meses
    
    Devuelve:
      - DataFrame de ventas con una nueva columna: 'Absorcion_prom_mensual'
    """
    ventas = ventas_df.copy()
    
    # Asegurar tipos datetime
    ventas[col_fecha_ventas] = pd.to_datetime(ventas[col_fecha_ventas])
    
    for df in [vertical_df, horizontal_df, lote_df]:
        if col_fecha_inicio in df.columns:
            df[col_fecha_inicio] = pd.to_datetime(df[col_fecha_inicio])
    
    # Función auxiliar para obtener tabla (Nombre_desarrollo -> Fecha_inicio_venta) por tipo
    def build_inicio_df(df_prod, tipo_label):
        if col_fecha_inicio not in df_prod.columns:
            return pd.DataFrame(columns=[col_desarrollo, col_fecha_inicio, col_tipo])
        
        tmp = df_prod[[col_desarrollo, col_fecha_inicio]].dropna().copy()
        # Si hay varias filas por desarrollo, nos quedamos con la fecha mínima (primer inicio)
        tmp = (
            tmp
            .sort_values(col_fecha_inicio)
            .drop_duplicates(subset=[col_desarrollo], keep="first")
        )
        tmp[col_tipo] = tipo_label
        return tmp
    
    inicio_vertical   = build_inicio_df(vertical_df,   "Vertical")
    inicio_horizontal = build_inicio_df(horizontal_df, "Horizontal")
    inicio_lote       = build_inicio_df(lote_df,       "Lote")
    
    inicio_todos = pd.concat(
        [inicio_vertical, inicio_horizontal, inicio_lote],
        ignore_index=True
    )
    
    # Unimos ventas con Fecha_inicio_venta según Tipo_proyecto + Nombre_desarrollo
    ventas = ventas.merge(
        inicio_todos,
        on=[col_desarrollo, col_tipo],
        how="left",
        suffixes=("", "_inicio")
    )
    
    # Ordenamos por proyecto, tipo y fecha
    ventas = ventas.sort_values([col_tipo, col_desarrollo, col_fecha_ventas]).reset_index(drop=True)
    
    # Fecha previa por proyecto y tipo (dentro de ventas_df)
    ventas["Fecha_prev"] = (
        ventas
        .groupby([col_tipo, col_desarrollo])[col_fecha_ventas]
        .shift(1)
    )
    
    # Para la primera fila de cada desarrollo, usamos Fecha_inicio_venta
    mask_first = ventas["Fecha_prev"].isna()
    ventas.loc[mask_first, "Fecha_prev"] = ventas.loc[mask_first, col_fecha_inicio]
    
    # Cálculo de meses de diferencia: (año*12 + mes)
    meses_diff = (
        ventas[col_fecha_ventas].dt.year * 12 + ventas[col_fecha_ventas].dt.month
        - (ventas["Fecha_prev"].dt.year * 12 + ventas["Fecha_prev"].dt.month)
    )
    
    # Evitar 0 o negativos (si algo raro pasa, ponemos 1 mes mínimo)
    meses_diff = meses_diff.clip(lower=1)
    
    ventas["Meses_periodo_calculados"] = meses_diff
    
    # Absorción promedio mensual
    ventas["Absorcion_prom_mensual"] = ventas[col_ventas_periodo] / ventas["Meses_periodo_calculados"]
    
    return ventas

# ============================================================
# Limpieza de datos
# ============================================================

# Se eliminan filas con 'Tipo_proyecto' nulo o '-'
ventas_df = ventas_df[ventas_df['Tipo_proyecto'].notna() & (ventas_df['Tipo_proyecto'] != '-')]
ventas_df = ventas_df.drop(columns=['Bloqueados', 'Apartados', 'Nota']).copy()

ventas_df = calcular_absorcion_mensual(
    ventas_df=ventas_df,
    vertical_df=vertical_df,
    horizontal_df=horizontal_df,
    lote_df=lote_df
)


# Proyectos atipicos a eliminar
ventas_df = ventas_df[~ventas_df["Nombre_desarrollo"].isin(['Monteverde', 
                                                            'Los Osuna Residencial - Etapa 2',
                                                            'Sonterra - Etapa 1',
                                                            'Monarca Residencial - Etapa 1',
                                                            'Los Osuna Residencial - Etapa 3',
                                                            'Monarca Residencial - Etapa 3',
                                                            'Paraíso Marina',
                                                            'Las Flores Residencial - Etapa 2',
                                                            'Las Primaveras Residencial',
                                                            'W Tower', 
                                                            'KM Cero'])].copy()


# Calculo de % vendido
ventas_df["%_vendido"] = ventas_df["Ventas_acumuladas"] /  ventas_df["Numero_de_viviendas_planeadas"] 

# Calcular meses en venta
ventas_df['Meses_en_venta'] = ((ventas_df['Fecha'].dt.year - ventas_df['Fecha_inicio_venta'].dt.year) * 12 + 
                          (ventas_df['Fecha'].dt.month - ventas_df['Fecha_inicio_venta'].dt.month))

# 2. Calcular el Periodo Relativo Calculamos la diferencia en meses entre la Venta y el Inicio del Proyecto GLOBAL
ventas_df['Periodo_relativo'] = ((ventas_df['Fecha'].dt.year - ventas_df['Fecha_inicio_venta'].dt.year) * 12 + 
                            (ventas_df['Fecha'].dt.month - ventas_df['Fecha_inicio_venta'].dt.month)) + 1 # +1 para indexar desde 1



# 1. Definición de Bins (Cortes) y Etiquetas
# El bin -1 asegura que el mes 0 quede incluido.
# float('inf') captura todo lo que sea mayor a 24 meses.
bins_fases = [-1, 6, 12, 24, float('inf')]

labels_fases = [
    'Lanzamiento',        # 0-6
    'Transición',         # 7-12
    'Maduración',         # 13-24
    'Tardía / Liq.'       # >24
]

# 2. Creación de la Variable Categórica
ventas_df['Fase_comercial'] = pd.cut(
    ventas_df['Meses_en_venta'], 
    bins=bins_fases, 
    labels=labels_fases
)

# 3. Optimización de Tipos (Crucial para ML y Gráficos)
# Convertimos explícitamente a categoría ordenada. 
# Esto le dice a Python (y a modelos como XGBoost/LightGBM) que hay una jerarquía.
ventas_df['Fase_comercial'] = ventas_df['Fase_comercial'].astype(
    pd.CategoricalDtype(categories=labels_fases, ordered=True)
)



# Aseguramos orden para que funciones como ffill() y shift() tengan sentido
ventas_df = ventas_df.sort_values(by=['Nombre_desarrollo', 'Periodo_relativo']).reset_index(drop=True)

# --- A. Meses_desde_ultima_venta (Recency) ---

# 1. Marcamos dónde hubo venta real (Booleano)
ventas_df['Hubo_venta'] = ventas_df['Ventas_periodo'] > 0

# 2. Identificamos el periodo relativo de esas ventas
#    Si Hubo_venta es False, ponemos NaN
ventas_df['Periodo_venta_activa'] = np.where(
    ventas_df['Hubo_venta'], 
    ventas_df['Periodo_relativo'], 
    np.nan
)

# 3. Propagamos hacia adelante (Forward Fill) el último periodo visto con venta
#    Esto responde: "¿Cuál fue el último 't' donde vendí?"
ventas_df['Ultimo_Periodo_Venta_Conocido'] = ventas_df.groupby('Nombre_desarrollo')['Periodo_venta_activa'].ffill()

# 4. Calculamos la diferencia
ventas_df['Meses_desde_ultima_venta'] = ventas_df['Periodo_relativo'] - ventas_df['Ultimo_Periodo_Venta_Conocido']

# 5. Manejo de Edge Cases (Inicios sin ventas)
#    Si nunca ha vendido (es NaN), asumimos que el tiempo de sequía es igual a su edad actual.
ventas_df['Meses_desde_ultima_venta'] = ventas_df['Meses_desde_ultima_venta'].fillna(ventas_df['Periodo_relativo']).astype(int)

# --- B. Lógica de Bloques de Fase (Para las variables 2 y 3) ---

# Detectamos cuándo cambia la fase respecto al mes anterior dentro del mismo proyecto
# True si cambió, False si es igual. El primer registro de cada grupo será True (o NaN que llenamos).
ventas_df['Cambio_fase_flag'] = ventas_df.groupby('Nombre_desarrollo')['Fase_comercial'].shift(1) != ventas_df['Fase_comercial']

# Creamos un ID único para cada "bloque" o "racha" de fase.
# Cumsum incrementa el ID cada vez que hay un cambio.
ventas_df['ID_Bloque_Fase'] = ventas_df.groupby('Nombre_desarrollo')['Cambio_fase_flag'].cumsum()

# --- C. Meses_desde_inicio_fase_actual ---

# Para cada bloque (proyecto + ID_bloque), encontramos el periodo mínimo (el inicio)
ventas_df['Inicio_Bloque_Periodo'] = ventas_df.groupby(['Nombre_desarrollo', 'ID_Bloque_Fase'])['Periodo_relativo'].transform('min')

# Resta simple
ventas_df['Meses_desde_inicio_fase_actual'] = ventas_df['Periodo_relativo'] - ventas_df['Inicio_Bloque_Periodo']



# --- D. Duracion_fase_anterior ---

# 1. Calculamos cuánto duró cada bloque (count)
duracion_bloques = ventas_df.groupby(['Nombre_desarrollo', 'ID_Bloque_Fase'])['Periodo_relativo'].count().reset_index()
duracion_bloques.rename(columns={'Periodo_relativo': 'Duracion_del_bloque_propio'}, inplace=True)

# 2. Desplazamos (Shift) la duración para obtener la del bloque ANTERIOR
duracion_bloques['Duracion_fase_anterior'] = duracion_bloques.groupby('Nombre_desarrollo')['Duracion_del_bloque_propio'].shift(1)

# 3. Cruzamos (Merge) esta información de vuelta al dataframe principal
#    Usamos 'left' para mantener todas las filas.
ventas_df = ventas_df.merge(
    duracion_bloques[['Nombre_desarrollo', 'ID_Bloque_Fase', 'Duracion_fase_anterior']],
    on=['Nombre_desarrollo', 'ID_Bloque_Fase'],
    how='left'
)

# 4. Llenamos nulos (la primera fase no tiene anterior, ponemos 0)
ventas_df['Duracion_fase_anterior'] = ventas_df['Duracion_fase_anterior'].fillna(0).astype(int)




# ---------------------------------------------------------
# 1. CAMBIO DE FASE
# ---------------------------------------------------------
# Lógica: Si la fase actual es distinta a la anterior, es un cambio.
# El primer registro de cada grupo dará NaN tras el shift, llenamos con False (0).

ventas_df['Cambio_de_fase'] = (
    ventas_df['Fase_comercial'] != ventas_df.groupby('Nombre_desarrollo')['Fase_comercial'].shift(1)
).astype(int)

# Corrección de borde: El primer mes de historia (Periodo 1) no es un "cambio", es el inicio.
# Forzamos a 0 el primer registro de cada grupo para limpieza.
ventas_df.loc[ventas_df.groupby('Nombre_desarrollo').head(1).index, 'Cambio_de_fase'] = 0

# 0. Aseguramos el orden estricto (Fundamental para shifts y rolling windows)
ventas_df = ventas_df.sort_values(by=['Nombre_desarrollo', 'Periodo_relativo']).reset_index(drop=True)

# ---------------------------------------------------------
# 2. REACTIVACIÓN COMERCIAL
# ---------------------------------------------------------
# Lógica: Venta > 0 HOY, pero Venta == 0 AYER y Venta == 0 ANTIER.

g = ventas_df.groupby('Nombre_desarrollo')['Ventas_periodo']

# Condiciones vectorizadas
cond_venta_hoy = ventas_df['Ventas_periodo'] > 0
cond_cero_ayer = g.shift(1) == 0
cond_cero_antier = g.shift(2) == 0

ventas_df['Reactivacion_comercial'] = (cond_venta_hoy & cond_cero_ayer & cond_cero_antier).astype(int)

# ---------------------------------------------------------
# 3. PERIODO PICO DE VENTAS (All-Time High)
# ---------------------------------------------------------
# Lógica: Ventas Hoy > Máximo Histórico acumulado hasta Ayer.

# Calculamos el máximo acumulado expansivo (running max) y lo desplazamos 1 mes
# para comparar "estrictamente" con el pasado, no con el presente incluido.
max_historico_previo = (
    ventas_df.groupby('Nombre_desarrollo')['Ventas_periodo']
    .expanding()
    .max()
    .groupby('Nombre_desarrollo') # Re-agrupar tras expanding para shift correcto
    .shift(1)
    .reset_index(level=0, drop=True) # Alinear índices
)

# Rellenamos NaN con -1 para que la primera venta (si es > 0) cuente como pico, 
# O puedes rellenar con un valor alto si NO quieres que el mes 1 sea pico.
# Aquí asumimos: Si el mes 1 vende 10, y el previo es NaN -> 10 > NaN es False. 
# Forzaremos manejo de nulos:
max_historico_previo = max_historico_previo.fillna(-1)

ventas_df['Periodo_pico_ventas'] = (ventas_df['Ventas_periodo'] > max_historico_previo).astype(int)


# ---------------------------------------------------------
# 4. INICIO DE DESACELERACIÓN
# ---------------------------------------------------------
# Lógica: Ventas caen por debajo del Promedio Móvil (3 meses), con margen de tolerancia.

WINDOW_SIZE = 3
TOLERANCIA = 0.05  # 5% de margen para evitar ruido (Recomendación profesional)

# Calculamos el promedio móvil de los ÚLTIMOS 3 meses (excluyendo el actual)
# Shift(1) mueve los datos un paso atrás, luego rolling(3) toma el promedio.
ma_pasado = (
    ventas_df.groupby('Nombre_desarrollo')['Ventas_periodo']
    .shift(1)
    .rolling(window=WINDOW_SIZE, min_periods=1) # min_periods=1 permite cálculo temprano
    .mean()
)

# Condición 1: Estamos "lentos" HOY? (Ventas < 95% del promedio pasado)
is_slow_today = ventas_df['Ventas_periodo'] < (ma_pasado * (1 - TOLERANCIA))

# Condición 2: Estábamos "lentos" AYER? (Para marcar solo el INICIO)
# Shiftamos el booleano 'is_slow_today'
was_slow_yesterday = is_slow_today.groupby(ventas_df['Nombre_desarrollo']).shift(1).fillna(False)

# Resultado: Es lento hoy Y NO era lento ayer
ventas_df['Inicio_desaceleracion'] = (is_slow_today & ~was_slow_yesterday).astype(int)


# Nos quedamos solo con las columnas relevantes para el análisis
ventas_df = ventas_df[
    ["Fecha", "Nombre_desarrollo", "Tipo_proyecto","Meses_en_venta","%_vendido",
     "Periodo_relativo",'Duracion_fase_anterior',"Fase_comercial",'Meses_desde_inicio_fase_actual',
     "Cambio_de_fase","Reactivacion_comercial","Periodo_pico_ventas","Inicio_desaceleracion", 
     "Meses_desde_ultima_venta", "Ventas_acumuladas","Ventas_periodo", "Absorcion_prom_mensual",
     "Inventario_disponible", "Numero_de_viviendas_planeadas","Ventas_detenidas",]].copy()


'''




# # ============================================================
# #   AGREGAR PRECIO PROMEDIO POR FECHA Y DESARROLLO
# #    (ignorando prototipos con precio = 0)
# # ============================================================

# # Aseguramos que la fecha sea datetime en ambos DF
# precios_df["Fecha"] = pd.to_datetime(precios_df["Fecha"])
# ventas_df["Fecha"] = pd.to_datetime(ventas_df["Fecha"])

# # --- 1) Columna de precio ---
# posibles_cols_precio = ["Precio"]
# col_precio = None
# for c in posibles_cols_precio:
#     if c in precios_df.columns:
#         col_precio = c
#         break

# if col_precio is None:
#     raise ValueError(
#         f"No se encontró ninguna columna de precio en precios_df. "
#         f"Revisa el nombre (ej. 'Precio', 'Precio_final'). "
#         f"Columnas disponibles: {precios_df.columns.tolist()}"
#     )

# # Convertimos a numérico por si viene como texto con símbolos
# precios_df[col_precio] = pd.to_numeric(precios_df[col_precio], errors="coerce")

# # --- 2) Filtrar precios > 0 para NO contarlos en el promedio ---
# precios_validos = precios_df[precios_df[col_precio] > 0].copy()

# # --- 3) Calcular precio promedio por Fecha + Nombre_desarrollo ---
# precios_promedio = (
#     precios_validos
#     .groupby(["Fecha", "Nombre_desarrollo"], as_index=False)[col_precio]
#     .mean()
#     .rename(columns={col_precio: "Precio_promedio"})
# )

# # --- Hacer el merge con ventas_con_abs_vf ---
# ventas_con_precio = ventas_df.merge(
#     precios_promedio,
#     on=["Fecha", "Nombre_desarrollo"],
#     how="left"
# )

# # ============================================================
# # 3.1 AGREGAR M2 PROMEDIO POR FECHA Y DESARROLLO
# #    (ignorando prototipos con M2 = 0)
# # ============================================================

# # --- 1) Elegir la columna de m2 ---
# posibles_cols_m2 = ["M2"]
# col_m2 = None
# for c in posibles_cols_m2:
#     if c in precios_df.columns:
#         col_m2 = c
#         break

# if col_m2 is None:
#     raise ValueError(
#         f"No se encontró ninguna columna de m2 en precios_df. "
#         f"Revisa el nombre (ej. 'M2', 'M2_construccion'). "
#         f"Columnas disponibles: {precios_df.columns.tolist()}"
#     )

# # Aseguramos tipo numérico
# precios_df[col_m2] = pd.to_numeric(precios_df[col_m2], errors="coerce")

# # --- 2) Filtrar m2 > 0 ---
# m2_validos = precios_df[precios_df[col_m2] > 0].copy()

# # --- 3) Calcular m2 promedio por Fecha + Nombre_desarrollo ---
# m2_promedio = (
#     m2_validos
#     .groupby(["Fecha", "Nombre_desarrollo"], as_index=False)[col_m2]
#     .mean()
#     .rename(columns={col_m2: "M2_promedio"})
# )

# # --- 4) Hacer el merge con ventas_con_precio ---
# ventas_con_precio = ventas_con_precio.merge(
#     m2_promedio,
#     on=["Fecha", "Nombre_desarrollo"],
#     how="left"
# )
 
# # ============================================================
# # 3.2 RELLENAR Precio_promedio CUANDO INVENTARIO = 0
# #     USANDO EL PRECIO PROMEDIO ANTERIOR (SI NO HAY VENTAS DETENIDAS)
# # ============================================================

# # Aseguramos que esté ordenado por desarrollo, tipo y fecha
# ventas_con_precio_M2 = ventas_con_precio.sort_values(
#     ["Nombre_desarrollo", "Tipo_proyecto", "Fecha"]
# ).reset_index(drop=True)

# # Crear una columna auxiliar con el forward-fill del precio por desarrollo+tipo
# ventas_con_precio_M2["Precio_promedio_ffill"] = (
#     ventas_con_precio_M2
#     .groupby(["Nombre_desarrollo", "Tipo_proyecto"])["Precio_promedio"]
#     .ffill()
# )

# # Crear una columna auxiliar con el forward-fill del precio por desarrollo+tipo
# ventas_con_precio_M2["M2_promedio_ffill"] = (
#     ventas_con_precio_M2
#     .groupby(["Nombre_desarrollo", "Tipo_proyecto"])["M2_promedio"]
#     .ffill()
# )

# # Máscara de filas donde queremos rellenar:
# # - Inventario_disponible == 0
# # - Precio_promedio es NaN
# # - Ventas_detenidas != 1
# mask_rellenar = (
#     (ventas_con_precio_M2["Inventario_disponible"] == 0) &
#     (ventas_con_precio_M2["Precio_promedio"].isna()) &
#     (ventas_con_precio_M2["Ventas_detenidas"] != 1)
# )

# # Aplicar el relleno solo en las filas que cumplen la condición
# ventas_con_precio_M2.loc[mask_rellenar, "Precio_promedio"] = \
#     ventas_con_precio_M2.loc[mask_rellenar, "Precio_promedio_ffill"]


# # Aplicar el relleno solo en las filas que cumplen la condición
# ventas_con_precio_M2.loc[mask_rellenar, "M2_promedio"] = \
#     ventas_con_precio_M2.loc[mask_rellenar, "M2_promedio_ffill"]

# # Eliminar columna auxiliar
# ventas_con_precio_M2 = ventas_con_precio_M2.drop(columns=["Precio_promedio_ffill", "M2_promedio_ffill"])

# #Calcular precio por M2
# ventas_con_precio_M2["Precio_por_M2"] = ventas_con_precio_M2["Precio_promedio"] / ventas_con_precio_M2["M2_promedio"]


# ventas_con_precio_M2.head(10)
'''
ventas_df.head(10)

C:\Users\julio\AppData\Local\Temp\ipykernel_25384\2863262390.py:357: FutureWarning: Downcasting object dtype arrays on .fillna, .ffill, .bfill is deprecated and will change in a future version. Call result.infer_objects(copy=False) instead. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  was_slow_yesterday = is_slow_today.groupby(ventas_df['Nombre_desarrollo']).shift(1).fillna(False)


Fecha Nombre_desarrollo Tipo_proyecto  Meses_en_venta  %_vendido  \
0 2023-10-01         5th Level      Vertical               1   0.208333   
1 2024-01-01         5th Level      Vertical               4   0.250000   
2 2024-04-01         5th Level      Vertical               7   0.250000   
3 2024-07-01         5th Level      Vertical              10   0.291667   
4 2024-10-01         5th Level      Vertical              13   0.250000   
5 2025-01-01         5th Level      Vertical              16   0.250000   
6 2025-04-01         5th Level      Vertical              19   0.291667   
7 2025-07-01         5th Level      Vertical              22   0.333333   
8 2025-10-01         5th Level      Vertical              25   0.375000   
9 2023-04-01             Adora      Vertical               0   0.039474   

   Periodo_relativo  Duracion_fase_anterior Fase_comercial  \
0                 2                       0    Lanzamiento   
1                 5                       0    Lanzamiento   
2                 8                       2     Transición   
3                11                       2     Transición   
4                14                       2     Maduración   
5                17                       2     Maduración   
6                20                       2     Maduración   
7                23                       2     Maduración   
8                26                       4  Tardía / Liq.   
9                 1                       0    Lanzamiento   

   Meses_desde_inicio_fase_actual  Cambio_de_fase  Reactivacion_comercial  \
0                               0               0                       0   
1                               3               0                       0   
2                               0               1                       0   
3                               3               0                       0   
4                               0               1                       0   
5                               3               0                       0   
6                               6               0                       1   
7                               9               0                       0   
8                               0               1                       0   
9                               0               0                       0   

   Periodo_pico_ventas  Inicio_desaceleracion  Meses_desde_ultima_venta  \
0                    1                      0                         0   
1                    0                      1                         0   
2                    0                      0                         3   
3                    0                      0                         0   
4                    0                      0                         3   
5                    0                      0                         6   
6                    0                      0                         0   
7                    0                      0                         0   
8                    0                      0                         0   
9                    1                      0                         0   

   Ventas_acumuladas  Ventas_periodo  Absorcion_prom_mensual  \
0                5.0             5.0                5.000000   
1                6.0             1.0                0.333333   
2                6.0             0.0                0.000000   
3                7.0             1.0                0.333333   
4                6.0             0.0                0.000000   
5                6.0             0.0                0.000000   
6                7.0             1.0                0.333333   
7                8.0             1.0                0.333333   
8                9.0             1.0                0.333333   
9                3.0             3.0                3.000000   

   Inventario_disponible  Numero_de_viviendas_planeadas  Ventas_detenidas  
0                   19.0                   